In [1]:
import numpy as np
import pandas as pd
import sklearn
import matplotlib.pyplot as plt
from astropy.table import Table
from astropy import units as u
from astropy import constants as const

In [2]:
cool_dwarfs = 'paper_iv_cool_dwarfs_for_girish.csv'
other_stuff = 'paper_iv_contaminating_stars_for_girish.csv'
gaia_crossmatch = 'k2_dr2_1arcsec.fits'
gaia_kepler_crossmatch = 'kepler_dr2_1arcsec.fits'

In [3]:
epic_1_df = pd.read_csv('epic_1_06July2018.txt', delimiter='|',
                        usecols=['id',
                                 'jmag', 'e_jmag',
                                 'hmag', 'e_hmag',
                                 'kmag', 'e_kmag'])
epic_2_df = pd.read_csv('epic_2_06July2018.txt', delimiter='|',
                        usecols=['id',
                                 'jmag', 'e_jmag',
                                 'hmag', 'e_hmag',
                                 'kmag', 'e_kmag'])
epic_3_df = pd.read_csv('epic_3_06July2018.txt', delimiter='|',
                        usecols=['id',
                                 'jmag', 'e_jmag',
                                 'hmag', 'e_hmag',
                                 'kmag', 'e_kmag'])
epic_4_df = pd.read_csv('epic_4_06July2018.txt', delimiter='|',
                        usecols=['id',
                                 'jmag', 'e_jmag',
                                 'hmag', 'e_hmag',
                                 'kmag', 'e_kmag'])
epic_5_df = pd.read_csv('epic_5_06July2018.txt', delimiter='|',
                        usecols=['id',
                                 'jmag', 'e_jmag',
                                 'hmag', 'e_hmag',
                                 'kmag', 'e_kmag'])
epic_6_df = pd.read_csv('epic_6_06July2018.txt', delimiter='|',
                        usecols=['id',
                                 'jmag', 'e_jmag',
                                 'hmag', 'e_hmag',
                                 'kmag', 'e_kmag'])

In [4]:
cd_df = pd.read_csv(cool_dwarfs)
cd_df = cd_df.drop([cd_df.index[13], cd_df.index[14],
                    cd_df.index[45], cd_df.index[46]])
cd_df = cd_df[np.array(cd_df['designation'], dtype=str) != 'nan']

os_df = pd.read_csv(other_stuff)
os_df = os_df.drop([os_df.index[64]])
os_df = os_df[np.array(os_df['designation'], dtype=str) != 'nan']
os_df = os_df[np.isfinite(os_df['EPIC_Teff'])]

gaia_df = Table.read(gaia_crossmatch, format='fits')

gaia_kepler_df = Table.read(gaia_kepler_crossmatch, format='fits')
teff_prov_arr = np.array(gaia_kepler_df['teff_prov'], dtype=str)
logg_prov_arr = np.array(gaia_kepler_df['logg_prov'], dtype=str)
teff_bool_arr = np.array(['SPE' in prov for prov in teff_prov_arr])
logg_bool_arr = np.array(['SPE' in prov for prov in logg_prov_arr])
both_bool_arr = teff_bool_arr & logg_bool_arr
gaia_kepler_df = gaia_kepler_df[both_bool_arr]
gaia_kepler_df = gaia_kepler_df[np.isfinite(gaia_kepler_df['phot_bp_mean_flux'])]
gaia_kepler_df = gaia_kepler_df[np.isfinite(gaia_kepler_df['phot_rp_mean_flux'])]
gaia_kepler_df = gaia_kepler_df[gaia_kepler_df['teff'] <= 12000]
gaia_kepler_df = gaia_kepler_df[gaia_kepler_df['source_id'] != 2053283126731961472]

In [5]:
catalog_columns = ['EPIC/KIC', 'GAIA_designation',
                   'T_e', 'err_T_e',
                   'log_g', 'err_log_g',
                   'feh', 'err_feh',
                   'parallax', 'err_parallax',
                   'gaia_g', 'err_gaia_g',
                   'gaia_b', 'err_gaia_b',
                   'gaia_r', 'err_gaia_r',
                   'jmag', 'err_jmag',
                   'hmag', 'err_hmag',
                   'kmag', 'err_kmag',
                   'pmra', 'err_pmra',
                   'pmdec', 'err_pmdec']
n_cols = len(catalog_columns)
os_rows = len(os_df['EPIC'])
cd_rows = len(cd_df['EPIC'])
kep_rows = len(gaia_kepler_df)
all_rows = os_rows + cd_rows + kep_rows

In [6]:
catalog_matrix = np.empty((all_rows, n_cols))

In [7]:
catalog_matrix[0:cd_rows, 0] = np.array(cd_df['EPIC'])
catalog_matrix[cd_rows:(os_rows + cd_rows), 0] = np.array(os_df['EPIC'])
catalog_matrix[(cd_rows + os_rows):, 0] = np.array(gaia_kepler_df['kepid'])

In [8]:
cd_test_arr = np.array([str(id_gaia)[9:] for id_gaia in cd_df['designation']])
os_test_arr = np.array([str(id_gaia)[9:] for id_gaia in os_df['designation']])

In [9]:
catalog_matrix[0:cd_rows, 1] = np.array(cd_test_arr, dtype=float)
catalog_matrix[cd_rows:(os_rows + cd_rows), 1] = np.array(os_test_arr, dtype=float)
catalog_matrix[(os_rows + cd_rows):, 1] = gaia_kepler_df['source_id']

In [10]:
catalog_matrix[0:cd_rows, 2] = cd_df['adopt_teff']
catalog_matrix[cd_rows:(os_rows + cd_rows), 2] = os_df['EPIC_Teff']
catalog_matrix[(os_rows + cd_rows):, 2] = gaia_kepler_df['teff']

In [11]:
catalog_matrix[0:cd_rows, 3] = np.max(np.array([cd_df['adopt_etefflo'], cd_df['adopt_eteffhi']]), axis=0)
catalog_matrix[cd_rows:(os_rows + cd_rows), 3] = 0.15*catalog_matrix[cd_rows:(os_rows + cd_rows), 2]
catalog_matrix[(os_rows + cd_rows):, 3] = np.max(np.array([gaia_kepler_df['teff_err1'], gaia_kepler_df['teff_err2']]), axis=0)

In [12]:
catalog_matrix[0:cd_rows, 4] = u.Dex(
    (const.G *
     (np.array(cd_df['adopt_ms']) * u.M_sun)
     / ((np.array(cd_df['adopt_rs']) * u.R_sun)**2)).cgs).value

ms_error = np.max(np.array([cd_df['adopt_emshi'], cd_df['adopt_emslo']]), axis=0)
rs_error = np.max(np.array([cd_df['adopt_ershi'], cd_df['adopt_erslo']]), axis=0)

catalog_matrix[0:cd_rows, 5] = np.sqrt(
    (ms_error/np.array(cd_df['adopt_ms']))**2.0
    + 4.0*(rs_error/np.array(cd_df['adopt_rs']))**2.0)/(np.log(10))

catalog_matrix[cd_rows:(os_rows + cd_rows), 4] = os_df['EPIC_logg']
catalog_matrix[cd_rows:(os_rows + cd_rows), 5][np.where(np.isfinite(catalog_matrix[cd_rows:(os_rows + cd_rows), 4]))] = 0.1
catalog_matrix[np.where(np.log10(catalog_matrix) <= -100.0)] = np.nan

catalog_matrix[(os_rows + cd_rows):, 4] = gaia_kepler_df['logg']
catalog_matrix[(os_rows + cd_rows):, 5] = np.nanmax(np.array([gaia_kepler_df['logg_err1'], gaia_kepler_df['logg_err2']]), axis=0)

/home/gmduvvuri/miniconda3/envs/astroconda/lib/python3.5/site-packages/ipykernel/__main__.py:15: RuntimeWarning: divide by zero encountered in log10
/home/gmduvvuri/miniconda3/envs/astroconda/lib/python3.5/site-packages/ipykernel/__main__.py:15: RuntimeWarning: invalid value encountered in less_equal
/home/gmduvvuri/miniconda3/envs/astroconda/lib/python3.5/site-packages/ipykernel/__main__.py:18: RuntimeWarning: All-NaN slice encountered


In [13]:
catalog_matrix[np.where(np.isnan(catalog_matrix[:, 5]))[0], 3] = catalog_matrix[np.where(np.isnan(catalog_matrix[:, 5]))[0], 2]*0.15
catalog_matrix[np.where(np.isnan(catalog_matrix[:, 5]))[0], 5] = 0.1

In [14]:
catalog_matrix[:cd_rows, 6] = cd_df['[Fe/H]']
catalog_matrix[:cd_rows, 7] = cd_df['e_[Fe/H]']

catalog_matrix[cd_rows:(cd_rows + os_rows), 6] = np.random.normal(scale=0.3)
catalog_matrix[cd_rows:(cd_rows + os_rows), 7] = 0.03

In [15]:
for designation, i in zip(cd_df['designation'], range(0, cd_rows)):
    mask_temp = np.where(gaia_df['designation'] == designation)[0]
    if len(mask_temp >= 1):
        catalog_matrix[i, 8] = gaia_df['parallax'][mask_temp[0]]
        catalog_matrix[i, 9] = gaia_df['parallax_error'][mask_temp[0]]
        catalog_matrix[i, 10] = gaia_df['phot_g_mean_mag'][mask_temp[0]]
        catalog_matrix[i, 12] = gaia_df['phot_bp_mean_mag'][mask_temp[0]]
        catalog_matrix[i, 14] = gaia_df['phot_rp_mean_mag'][mask_temp[0]]
        catalog_matrix[i, 22] = gaia_df['pmra'][mask_temp[0]]
        catalog_matrix[i, 23] = gaia_df['pmra_error'][mask_temp[0]]
        catalog_matrix[i, 24] = gaia_df['pmdec'][mask_temp[0]]
        catalog_matrix[i, 25] = gaia_df['pmdec_error'][mask_temp[0]]
    else:
        catalog_matrix[i, 8:] = np.nan

for designation, i in zip(os_df['designation'], range(cd_rows,
                                                      cd_rows + os_rows)):
    mask_temp = np.where(gaia_df['designation'] == designation)[0]
    if len(mask_temp >= 1):
        catalog_matrix[i, 8] = gaia_df['parallax'][mask_temp[0]]
        catalog_matrix[i, 9] = gaia_df['parallax_error'][mask_temp[0]]
        catalog_matrix[i, 10] = gaia_df['phot_g_mean_mag'][mask_temp[0]]
        catalog_matrix[i, 12] = gaia_df['phot_bp_mean_mag'][mask_temp[0]]
        catalog_matrix[i, 14] = gaia_df['phot_rp_mean_mag'][mask_temp[0]]
    else:
        catalog_matrix[i, 8:] = np.nan

catalog_matrix[cd_rows + os_rows:, 8] = gaia_kepler_df['parallax']
catalog_matrix[cd_rows + os_rows:, 9] = gaia_kepler_df['parallax_error']
catalog_matrix[cd_rows + os_rows:, 10] = gaia_kepler_df['phot_g_mean_mag']
catalog_matrix[cd_rows + os_rows:, 12] = gaia_kepler_df['phot_bp_mean_mag']
catalog_matrix[cd_rows + os_rows:, 14] = gaia_kepler_df['phot_rp_mean_mag']
catalog_matrix[cd_rows + os_rows:, 16] = gaia_kepler_df['jmag']
catalog_matrix[cd_rows + os_rows:, 17] = 0.03
catalog_matrix[cd_rows + os_rows:, 18] = gaia_kepler_df['hmag']
catalog_matrix[cd_rows + os_rows:, 19] = 0.03
catalog_matrix[cd_rows + os_rows:, 20] = gaia_kepler_df['kmag']
catalog_matrix[cd_rows + os_rows:, 21] = 0.03
catalog_matrix[cd_rows + os_rows:, 22] = gaia_kepler_df['pmra']
catalog_matrix[cd_rows + os_rows:, 23] = gaia_kepler_df['pmra_error']
catalog_matrix[cd_rows + os_rows:, 24] = gaia_kepler_df['pmdec']
catalog_matrix[cd_rows + os_rows:, 25] = gaia_kepler_df['pmdec_error']

In [16]:
catalog_matrix[:, 11][np.where(catalog_matrix[:, 10] < 16.0)] = 0.0002
catalog_matrix[:, 11][np.where((catalog_matrix[:, 10] >= 16.0)
                              & (catalog_matrix[:, 10] < 17.0))] = 0.0004
catalog_matrix[:, 11][np.where((catalog_matrix[:, 10] >= 17.0)
                              & (catalog_matrix[:, 10] < 18.0))] = 0.0006
catalog_matrix[:, 11][np.where((catalog_matrix[:, 10] >= 18.0)
                              & (catalog_matrix[:, 10] < 19.0))] = 0.0009
catalog_matrix[:, 11][np.where((catalog_matrix[:, 10] >= 19.0)
                              & (catalog_matrix[:, 10] < 20.0))] = 0.0018

catalog_matrix[:, 13][np.where(catalog_matrix[:, 12] < 14.0)] = 0.001
catalog_matrix[:, 13][np.where((catalog_matrix[:, 12] >= 14.0)
                              & (catalog_matrix[:, 12] < 15.0))] = 0.002
catalog_matrix[:, 13][np.where((catalog_matrix[:, 12] >= 15.0)
                              & (catalog_matrix[:, 12] < 16.0))] = 0.005
catalog_matrix[:, 13][np.where((catalog_matrix[:, 12] >= 16.0)
                              & (catalog_matrix[:, 12] < 17.0))] = 0.01
catalog_matrix[:, 13][np.where((catalog_matrix[:, 12] >= 17.0)
                              & (catalog_matrix[:, 12] < 18.0))] = 0.025
catalog_matrix[:, 13][np.where((catalog_matrix[:, 12] >= 18.0)
                              & (catalog_matrix[:, 12] < 19.0))] = 0.063
catalog_matrix[:, 13][np.where((catalog_matrix[:, 12] >= 19.0)
                              & (catalog_matrix[:, 12] < 20.0))] = 0.157
catalog_matrix[:, 13][np.where((catalog_matrix[:, 12] >= 20.0)
                              & (catalog_matrix[:, 12] < 21.0))] = 0.395

catalog_matrix[:, 15][np.where(catalog_matrix[:, 14] < 15.0)] = 0.001
catalog_matrix[:, 15][np.where((catalog_matrix[:, 14] >= 15.0)
                              & (catalog_matrix[:, 14] < 16.0))] = 0.002
catalog_matrix[:, 15][np.where((catalog_matrix[:, 14] >= 16.0)
                              & (catalog_matrix[:, 14] < 17.0))] = 0.003
catalog_matrix[:, 15][np.where((catalog_matrix[:, 14] >= 17.0)
                              & (catalog_matrix[:, 14] < 18.0))] = 0.006
catalog_matrix[:, 15][np.where((catalog_matrix[:, 14] >= 18.0)
                              & (catalog_matrix[:, 14] < 19.0))] = 0.015
catalog_matrix[:, 15][np.where((catalog_matrix[:, 14] >= 19.0)
                              & (catalog_matrix[:, 14] < 20.0))] = 0.037



In [17]:
catalog_matrix[np.where(catalog_matrix[:, 3] >= 200000)[0], 3] = 0.15*catalog_matrix[np.where(catalog_matrix[:, 3] >= 200000)[0], 2]

In [18]:
for i in range(0, cd_rows+os_rows):
    kepler_id = catalog_matrix[i, 0]
    if kepler_id <= 210000000:
        temp_df = epic_1_df
    elif kepler_id <= 220000000:
        temp_df = epic_2_df
    elif kepler_id <= 230000000:
        temp_df = epic_3_df
    elif kepler_id <= 240000000:
        temp_df = epic_4_df
    elif kepler_id <= 250000000:
        temp_df = epic_5_df
    else:
        temp_df = epic_6_df
    catalog_matrix[i, 16] = temp_df.loc[temp_df['id'] == kepler_id]['jmag']
    catalog_matrix[i, 17] = temp_df.loc[temp_df['id'] == kepler_id]['e_jmag']
    catalog_matrix[i, 18] = temp_df.loc[temp_df['id'] == kepler_id]['hmag']
    catalog_matrix[i, 19] = temp_df.loc[temp_df['id'] == kepler_id]['e_hmag']
    catalog_matrix[i, 20] = temp_df.loc[temp_df['id'] == kepler_id]['kmag']
    catalog_matrix[i, 21] = temp_df.loc[temp_df['id'] == kepler_id]['e_kmag']

In [19]:
epic_1_apply_df = epic_1_df[np.isfinite(epic_1_df['jmag'])
                            & np.isfinite(epic_1_df['hmag'])
                            & np.isfinite(epic_1_df['kmag'])]
epic_2_apply_df = epic_2_df[np.isfinite(epic_2_df['jmag'])
                            & np.isfinite(epic_2_df['hmag'])
                            & np.isfinite(epic_2_df['kmag'])]
epic_3_apply_df = epic_3_df[np.isfinite(epic_3_df['jmag'])
                            & np.isfinite(epic_3_df['hmag'])
                            & np.isfinite(epic_3_df['kmag'])]
epic_4_apply_df = epic_4_df[np.isfinite(epic_4_df['jmag'])
                            & np.isfinite(epic_4_df['hmag'])
                            & np.isfinite(epic_4_df['kmag'])]
epic_5_apply_df = epic_5_df[np.isfinite(epic_5_df['jmag'])
                            & np.isfinite(epic_5_df['hmag'])
                            & np.isfinite(epic_5_df['kmag'])]
epic_6_apply_df = epic_6_df[np.isfinite(epic_6_df['jmag'])
                            & np.isfinite(epic_6_df['hmag'])
                            & np.isfinite(epic_6_df['kmag'])]

In [20]:
apply_df = gaia_df[np.isfinite(gaia_df['parallax'])
                   & np.isfinite(gaia_df['phot_g_mean_mag'])
                   & np.isfinite(gaia_df['phot_bp_mean_mag'])
                   & np.isfinite(gaia_df['phot_rp_mean_mag'])]
apply_df = apply_df.to_pandas()

In [21]:
for i in range(0, cd_rows+os_rows):
#    apply_df = apply_df[apply_df['epic_number'] != np.array(catalog_matrix[:, 0], dtype=int)[i]]
    apply_df.drop(np.where(apply_df['epic_number'] == int(catalog_matrix[i, 0]))[0][0])

In [22]:
apply_matrix = np.empty((len(apply_df), n_cols))
apply_matrix[:, 0] = apply_df['epic_number']
apply_matrix[:, 1] = apply_df['source_id']
apply_matrix[:, 2] = np.nan
apply_matrix[:, 3] = np.nan
apply_matrix[:, 4] = np.nan
apply_matrix[:, 5] = np.nan
apply_matrix[:, 6] = np.nan
apply_matrix[:, 7] = np.nan
apply_matrix[:, 8] = apply_df['parallax']
apply_matrix[:, 9] = apply_df['parallax_error']
apply_matrix[:, 10] = apply_df['phot_g_mean_mag']
apply_matrix[:, 12] = apply_df['phot_bp_mean_mag']
apply_matrix[:, 14] = apply_df['phot_rp_mean_mag']
apply_matrix[:, 22] = apply_df['pmra']
apply_matrix[:, 23] = apply_df['pmra_error']
apply_matrix[:, 24] = apply_df['pmdec']
apply_matrix[:, 25] = apply_df['pmdec_error']
valid_ids = np.empty((len(apply_df)), dtype=bool)

def fill_up(i):
    kepler_id = apply_df['epic_number'][i]
    if kepler_id <= 210000000:
        temp_df = epic_1_apply_df
    elif kepler_id <= 220000000:
        temp_df = epic_2_apply_df
    elif kepler_id <= 230000000:
        temp_df = epic_3_apply_df
    elif kepler_id <= 240000000:
        temp_df = epic_4_apply_df
    elif kepler_id <= 250000000:
        temp_df = epic_5_apply_df
    else:
        temp_df = epic_6_apply_df
    if kepler_id in np.array(temp_df['id']):
        valid_ids[i] = True
        apply_matrix[i, 16] = temp_df[temp_df['id'] == kepler_id]['jmag']
        apply_matrix[i, 17] = temp_df[temp_df['id'] == kepler_id]['e_jmag']
        apply_matrix[i, 18] = temp_df[temp_df['id'] == kepler_id]['hmag']
        apply_matrix[i, 19] = temp_df[temp_df['id'] == kepler_id]['e_hmag']
        apply_matrix[i, 20] = temp_df[temp_df['id'] == kepler_id]['kmag']
        apply_matrix[i, 21] = temp_df[temp_df['id'] == kepler_id]['e_kmag']
    else:
        valid_ids[i] = False
        apply_matrix[i, 16] = np.nan
        apply_matrix[i, 17] = np.nan
        apply_matrix[i, 18] = np.nan
        apply_matrix[i, 19] = np.nan
        apply_matrix[i, 20] = np.nan
        apply_matrix[i, 21] = np.nan

from multiprocessing import Pool, cpu_count

pool_map = Pool(cpu_count() - 1)

pool_map.map(fill_up, range(len(apply_df)))

201314724.0
60017806.0
201588656.0
201871706.0
202586991.0
204351607.0
205991136.0
206461117.0
60017809.0
60017810.0
201314772.0
60017812.0
201871727.0
202587982.0
201588671.0
205991257.0
204351607.0
60017814.0
206461200.0
60017815.0
60017816.0
201314796.0
60017818.0
202588237.0
201871728.0
205991327.0
201588741.0
60017821.0
202589741.0
60017822.0
201871754.0
204351607.0
201314832.0
60017827.0
206461269.0
201314889.0
60017836.0
205991391.0
60017839.0
201588771.0
60017850.0
202589809.0
204351804.0
60017852.0
201871769.0
60017853.0
205991396.0
201314911.0
206461416.0
204352020.0
60017854.0
60017873.0
201588787.0
60017877.0
202589921.0
201871840.0
201314928.0
60017886.0
206461468.0
204352176.0
205991433.0
60017887.0
60017892.0
205991454.0
201588798.0
60017893.0
202590030.0
204352341.0
201871915.0
60017898.0
201588910.0
206461725.0
201315010.0
60017901.0
60017902.0
202590141.0
60017908.0
205991466.0
201871924.0
60017912.0
201588953.0
201315038.0
60017924.0
204352341.0
206461776.0
202590160

206465746.0
201590650.0
205993318.0
60018855.0
60018857.0
204360645.0
60018858.0
60018864.0
206465769.0
201318126.0
205993356.0
201590700.0
201874549.0
202606089.0
60018865.0
204360961.0
60018866.0
202606214.0
201590711.0
60018867.0
201318154.0
201874567.0
201590714.0
60018872.0
205993384.0
204361003.0
60018873.0
206465829.0
202606391.0
201590724.0
60018875.0
201874573.0
201874592.0
201318165.0
60018881.0
204361038.0
205993403.0
201590725.0
202606496.0
60018882.0
206465925.0
204361087.0
60018883.0
60018899.0
201874618.0
201318197.0
60018900.0
205993418.0
204361349.0
202606769.0
60018900.0
206465953.0
205993454.0
201590752.0
201590753.0
60018903.0
60018908.0
201318314.0
201874678.0
204361925.0
60018909.0
202606921.0
206466118.0
60018910.0
60018911.0
201590795.0
201318343.0
205993475.0
60018912.0
201874744.0
204361957.0
60018913.0
202607155.0
60018944.0
60018945.0
204362132.0
201318538.0
206466176.0
201590825.0
205993484.0
201874759.0
202607322.0
60018947.0
201318587.0
60018949.0
2064661

60019650.0
206469879.0
201592218.0
204369703.0
205994943.0
60019651.0
60019652.0
201877511.0
60019655.0
202626916.0
201321012.0
60019658.0
60019683.0
206469897.0
205994961.0
201877513.0
201592238.0
60019685.0
204369791.0
60019711.0
202627120.0
206470130.0
205995047.0
201592240.0
60019718.0
201877674.0
60019719.0
201321030.0
60019720.0
204370146.0
60019721.0
206470153.0
205995057.0
202627452.0
201877780.0
201592246.0
201321031.0
60019723.0
60019724.0
204370385.0
60019727.0
206470214.0
60019729.0
201877821.0
201592262.0
202627477.0
201321047.0
60019733.0
205995088.0
60019735.0
204370527.0
201321074.0
60019738.0
202627715.0
60019740.0
201877822.0
206470267.0
201592270.0
60019741.0
204371449.0
60019742.0
201877965.0
201321113.0
205995091.0
202627721.0
206470277.0
60019743.0
204371512.0
202628447.0
60019763.0
205995150.0
201877976.0
60019764.0
201592300.0
204371613.0
206470389.0
201321203.0
60019765.0
202628742.0
60019766.0
206470393.0
201878009.0
60019768.0
201592328.0
60019770.0
204371762

60020413.0
60020414.0
201593566.0
60020415.0
204377698.0
60020416.0
201880016.0
205997245.0
202639882.0
60020424.0
206474637.0
201323613.0
60020426.0
201880058.0
60020427.0
204377731.0
201593629.0
201593643.0
60020428.0
202640186.0
60020429.0
205997248.0
206474695.0
201323727.0
60020430.0
201880062.0
201593650.0
204377821.0
60020433.0
201323758.0
202640267.0
60020436.0
205997312.0
206474784.0
201593658.0
60020438.0
201323762.0
60020462.0
201880134.0
205997313.0
204378994.0
202640521.0
60020463.0
206474831.0
60020467.0
201593659.0
201880146.0
60020468.0
201323771.0
60020469.0
202640668.0
204378998.0
205997437.0
60020470.0
206475021.0
201593699.0
201880326.0
201323857.0
60020472.0
60020473.0
202640735.0
204379009.0
205997464.0
201593700.0
206475150.0
201880343.0
60020475.0
60020476.0
60020477.0
201323863.0
205997466.0
202640826.0
60020478.0
60020479.0
201323881.0
204379173.0
201593707.0
60020480.0
206475309.0
201880397.0
205997501.0
60020485.0
201323936.0
206475525.0
60020490.0
202641232

204386649.0
60021237.0
202655106.0
206479394.0
205999322.0
60021239.0
60021240.0
201881985.0
201326857.0
60021241.0
201595699.0
205999340.0
204386649.0
202655145.0
60021243.0
206479626.0
201881998.0
60021256.0
201326870.0
201595774.0
60021260.0
202655495.0
204386649.0
201326984.0
60021261.0
205999344.0
206479633.0
60021262.0
201595781.0
60021264.0
201882011.0
60021268.0
202655569.0
60021270.0
60021278.0
60021281.0
205999354.0
201327005.0
206479739.0
60021282.0
204386649.0
201327090.0
201595783.0
60021288.0
201882012.0
60021333.0
202655586.0
60021336.0
206479772.0
60021337.0
201595789.0
205999380.0
206479862.0
201882026.0
204387048.0
201327123.0
60021338.0
202655918.0
60021340.0
60021341.0
60021344.0
206480011.0
60021345.0
205999405.0
60021346.0
201595795.0
201882087.0
204387136.0
201327123.0
60021347.0
202656096.0
60021348.0
206480032.0
60021356.0
60021360.0
205999437.0
202656205.0
201595813.0
60021362.0
201882093.0
204387136.0
201327123.0
60021363.0
201882149.0
202656282.0
60021365.0


...

247829731.0
249271182.0
247829994.0
249780361.0
248690897.0
249271330.0
248690898.0
249780393.0
247830256.0
249271343.0
249780470.0
248690937.0
249271394.0
247830259.0
249780485.0
249271451.0
248691017.0
249271541.0
248691071.0
249271592.0
249780496.0
247830504.0
247830700.0
248691112.0
247831179.0
249271595.0
248691117.0
247831425.0
249780576.0
249271720.0
249271788.0
248691154.0
248691257.0
247831507.0
249780590.0
249271853.0
248691307.0
248691369.0
247831572.0
249271909.0
249780687.0
249271933.0
248691409.0
249780694.0
247831573.0
249271962.0
249780720.0
248691434.0
247831575.0
249272013.0
247831611.0
249780753.0
248691446.0
249272097.0
247832255.0
247832534.0
249272200.0
249780766.0
248691525.0
247832592.0
249780775.0
249272239.0
248691543.0
247832939.0
249780787.0
247833111.0
249272602.0
248691643.0
249780791.0
249272654.0
247833205.0
248691644.0
249780855.0
248691666.0
249272686.0
247833271.0
249780951.0
247833383.0
248691772.0
249780961.0
249272727.0
247833506.0
249781046.0
2486

249788157.0
247856861.0
249325370.0
249788175.0
247857136.0
249788176.0
249325470.0
249788177.0
247857331.0
249325682.0
249788248.0
249325800.0
249788249.0
247857372.0
249325815.0
247857562.0
249788281.0
249325953.0
247857741.0
249788284.0
249326022.0
247858133.0
247858309.0
249326054.0
249788474.0
247858390.0
249326097.0
249788556.0
247858453.0
249326163.0
249788566.0
247858609.0
249326298.0
249788681.0
247858707.0
247858829.0
249326576.0
249788701.0
247859013.0
249788724.0
249326613.0
247859143.0
249788771.0
249326633.0
249326788.0
249788781.0
247859165.0
249788855.0
249326843.0
247859663.0
249788962.0
249326847.0
247859832.0
249788990.0
249326856.0
247859850.0
249789028.0
249326892.0
247860066.0
249789038.0
249326965.0
247860109.0
249789045.0
249326990.0
247860367.0
249789108.0
249327145.0
249789143.0
247860402.0
249789168.0
249327335.0
247860620.0
249789172.0
247860817.0
249327394.0
247860837.0
249789196.0
249327506.0
247860961.0
249789208.0
249327571.0
247861033.0
249789219.0
2493

247889315.0
249797631.0
249340779.0
247889435.0
249340874.0
247889456.0
249797642.0
247889515.0
249340983.0
247889550.0
249797653.0
249341095.0
247889867.0
249797682.0
249341126.0
247889905.0
249797689.0
249341174.0
247890040.0
249797749.0
247890227.0
249341227.0
249797755.0
247890247.0
249341234.0
249797811.0
247890450.0
249341347.0
247890573.0
249797814.0
249341378.0
247890584.0
249797828.0
249341451.0
247890803.0
249797878.0
247890915.0
249341493.0
249797884.0
249341537.0
249797916.0
247891121.0
249797935.0
249341562.0
247891303.0
249798042.0
249798355.0
249341623.0
249798359.0
249341641.0
249341670.0
249798364.0
249341677.0
249798522.0
249798526.0
249341725.0
249798527.0
249341762.0
249798691.0
249341794.0
249798694.0
249341795.0
249798769.0
249341840.0
249798788.0
249341913.0
249341944.0
249798838.0
249342002.0
249798863.0
249342036.0
249798872.0
249342118.0
249798885.0
249342126.0
249798954.0
249342204.0
249799015.0
249799036.0
249342225.0
249799050.0
249342313.0
249342415.0
2497

249816509.0
249816522.0
249816539.0
249816546.0
249816647.0
249816655.0
249816686.0
249816733.0
249816822.0
249816854.0
249816891.0
249816948.0
249816953.0
249816994.0
249817095.0
249817102.0
249817151.0
249817220.0
249817235.0
249817236.0
249817238.0
249817261.0
249817473.0
249817504.0
249817512.0
249817611.0
249817633.0
249817638.0
249817722.0
249817863.0
249817893.0
249817940.0
249817942.0
249817987.0
249817993.0
249818019.0
249818064.0
249818078.0
249818206.0
249818229.0
249818282.0
249818387.0
249818409.0
249818472.0
249818514.0
249818532.0
249818597.0


[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

In [23]:
apply_matrix_final = apply_matrix[valid_ids, :]

In [26]:
sample_cloud_num = 100
cloud_df = pd.DataFrame(columns=['ID','T_e', 'log_g', 'feh',
                                 'parallax', 'gaia_g', 'gaia_b', 'gaia_r',
                                 'jmag', 'hmag', 'kmag'],
                        index=range(len(apply_matrix_final)*sample_cloud_num))

for i in range(0, len(apply_matrix_final)):
    cloud_df['ID'].iloc[i*sample_cloud_num: (i+1)*sample_cloud_num]= apply_matrix_final[i, 0]
    cloud_df['T_e'].iloc[i*sample_cloud_num: (i+1)*sample_cloud_num] = np.random.normal(loc=apply_matrix_final[i, 2], scale=apply_matrix_final[i, 3], size=sample_cloud_num)
    cloud_df['log_g'].iloc[i*sample_cloud_num: (i+1)*sample_cloud_num] = np.random.normal(loc=apply_matrix_final[i, 4], scale=apply_matrix_final[i, 5], size=sample_cloud_num)
    cloud_df['feh'].iloc[i*sample_cloud_num: (i+1)*sample_cloud_num] = np.random.normal(loc=apply_matrix_final[i, 6], scale=apply_matrix_final[i, 7], size=sample_cloud_num)
    cloud_df['parallax'].iloc[i*sample_cloud_num: (i+1)*sample_cloud_num] = np.random.normal(loc=apply_matrix_final[i, 8], scale=apply_matrix_final[i, 9], size=sample_cloud_num)
    cloud_df['gaia_g'].iloc[i*sample_cloud_num: (i+1)*sample_cloud_num] = np.random.normal(loc=apply_matrix_final[i, 10], scale=apply_matrix_final[i, 11], size=sample_cloud_num)
    cloud_df['gaia_b'].iloc[i*sample_cloud_num: (i+1)*sample_cloud_num] = np.random.normal(loc=apply_matrix_final[i, 12], scale=apply_matrix_final[i, 13], size=sample_cloud_num)
    cloud_df['gaia_r'].iloc[i*sample_cloud_num: (i+1)*sample_cloud_num] = np.random.normal(loc=apply_matrix_final[i, 14], scale=apply_matrix_final[i, 15], size=sample_cloud_num)
    cloud_df['jmag'].iloc[i*sample_cloud_num: (i+1)*sample_cloud_num] = np.random.normal(loc=apply_matrix_final[i, 16], scale=apply_matrix_final[i, 17], size=sample_cloud_num)
    cloud_df['hmag'].iloc[i*sample_cloud_num: (i+1)*sample_cloud_num] = np.random.normal(loc=apply_matrix_final[i, 18], scale=apply_matrix_final[i, 19], size=sample_cloud_num)
    cloud_df['kmag'].iloc[i*sample_cloud_num: (i+1)*sample_cloud_num] = np.random.normal(loc=apply_matrix_final[i, 20], scale=apply_matrix_final[i, 21], size=sample_cloud_num)

/home/gmduvvuri/miniconda3/envs/astroconda/lib/python3.5/site-packages/pandas/core/indexing.py:189: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._setitem_with_indexer(indexer, value)


In [28]:
cloud_matrix = np.array(cloud_df)
cloud_matrix

array([[60017806, nan, nan, ..., 0, 0, 0],
       [60017806, nan, nan, ..., 0, 0, 0],
       [60017806, nan, nan, ..., 0, 0, 0],
       ..., 
       [201110617, nan, nan, ..., 0, 0, 0],
       [201110617, nan, nan, ..., 0, 0, 0],
       [201110617, nan, nan, ..., 0, 0, 0]], dtype=object)

In [ ]:
X_k2 = catalog_matrix[:(cd_rows + os_rows), np.arange(8, 22, 2)]
X_kepler = catalog_matrix[(cd_rows + os_rows):, np.arange(8, 22, 2)]

y_k2 = catalog_matrix[:(cd_rows + os_rows), [2, 4]]
y_kepler = catalog_matrix[(cd_rows + os_rows):, [2, 4]]




In [ ]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import ExtraTreesRegressor
from sklearn.ensemble import AdaBoostRegressor
from sklearn.multioutput import MultiOutputRegressor
from sklearn.model_selection import train_test_split

In [ ]:
train_frac = 0.8
test_frac = 1.0 - train_frac
X_train_k2, X_test_k2, y_train_k2, y_test_k2 = train_test_split(X_k2, y_k2, train_size=train_frac, test_size=test_frac)
X_train_kep, X_test_kep, y_train_kep, y_test_kep = train_test_split(X_kepler, y_kepler, train_size=train_frac, test_size=test_frac)

In [ ]:
X_test = np.append(X_test_k2, X_test_kep, axis=0)
X_train = np.append(X_train_k2, X_train_kep, axis=0)


y_test = np.append(y_test_k2, y_test_kep, axis=0)
y_train = np.append(y_train_k2, y_train_kep, axis=0)

# X_test = X_test_k2
# X_train = X_train_k2

# y_test= y_test_k2
# y_train = y_train_k2

In [ ]:
regr_multirf = MultiOutputRegressor(RandomForestRegressor(n_estimators=500,
                                    random_state=0))
regr_multirf.fit(X_train, y_train)

In [ ]:
y_multirf = regr_multirf.predict(X_test)

In [ ]:
plt.scatter(y_test[:, 0], y_test[:, 1], label='True')
# plt.scatter(y_train[:, 0], y_train[:, 1], label='Train', alpha=0.2)
plt.scatter(y_multirf[:, 0], y_multirf[:, 1], label='Predicted, score= ' + str(regr_multirf.score(X_test, y_test)), alpha=0.2)
plt.xlabel(r'$T_e$')
plt.ylabel(r'log g')
plt.ylim(4.0, 5.5)
plt.legend()
plt.savefig('prelim_rf_test.pdf')
plt.show()

In [ ]:
cd_num = np.shape(y_test_k2)[0]
cd_num_2 = np.shape(y_train_k2)[0]

In [ ]:
# plt.scatter((y_test[:cd_num, 0] - y_multirf[:cd_num, 0])/(y_test[:cd_num, 0]), (y_test[:cd_num, 1]- y_multirf[:cd_num, 1])/(y_test[:cd_num, 1]), label='True')
plt.scatter((y_test[:, 0] - y_multirf[:, 0])/(y_test[:, 0]), (y_test[:, 1]- y_multirf[:, 1])/(y_test[:, 1]), label='True')
# plt.scatter(y_train[:, 0], y_train[:, 1], label='Train', alpha=0.2)
#plt.scatter(y_multirf[:, 0], y_multirf[:, 1], label='Predicted, score= ' + str(regr_multirf.score(X_test, y_test)), alpha=0.2)
plt.xlabel(r'$T_e$')
plt.ylabel(r'log g')
plt.legend()
plt.show()

In [ ]:
regr_multirf.score(X_test[:cd_num, :], y_test[:cd_num, :])

In [ ]:
# plt.scatter(y_test[:cd_num, 0], y_test[:cd_num, 1])
# plt.scatter(y_train[:cd_num_2, 0], y_train[:cd_num_2, 1])
plt.scatter(y_test[:cd_num, 0], y_test[:cd_num, 1])
plt.scatter(y_multirf[:cd_num, 0], y_multirf[:cd_num, 1])